<a href="https://colab.research.google.com/github/nicktheslumpgod/CuseHacksDatathon2025/blob/main/SYRCityline_Heatmaps.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [135]:
import pandas as pd
import folium
from folium.plugins import HeatMap, HeatMapWithTime


# single comment generated by OpenAI ChatGPT-o3-mni-high
# Load your dataset
# For example, if your data is in a CSV file:
df = pd.read_csv("/content/SYRCityline_Requests_(2021-Present)_Cleaned.csv")

# Convert the Created_at_local column to datetime
df['Created_at_local'] = pd.to_datetime(df['Created_at_local'])

# Group the data by location to count the number of events at each coordinate
heat_data = df.groupby(['Lat', 'Lng']).size().reset_index(name='count')

# Create a list of points in the format [latitude, longitude, weight]
heat_list = heat_data[['Lat', 'Lng', 'count']].values.tolist()

# Determine the center of the map based on the data
map_center = [df['Lat'].mean(), df['Lng'].mean()]

m = folium.Map(location=map_center,
               control_scale=True,
               zoom_control=False,
               zoom_start=12)

HeatMap(heat_list, radius=15,).add_to(m)

# Save the map to an HTML file (or display it in a Jupyter notebook)
m.save('heatmap.html')

m

In [136]:
import pandas as pd
import geopandas as gpd
import folium

# --- Load Ticket Data (Points) ---
df = pd.read_csv("/content/SYRCityline_Requests_(2021-Present)_Cleaned.csv")
# Create a GeoDataFrame from the ticket data. Adjust column names if necessary.
gdf_points = gpd.GeoDataFrame(
    df,
    geometry=gpd.points_from_xy(df.Lng, df.Lat),
    crs="EPSG:4326"
)

# --- Load TNT_Areas Data (Polygons) ---
tnt_areas = gpd.read_file('/content/Syracuse_TNT_Areas.geojson')
if tnt_areas.crs is None or tnt_areas.crs.to_string() != 'EPSG:4326':
    tnt_areas = tnt_areas.to_crs(epsg=4326)

# --- Spatial Join: Assign Each Ticket Its TNT_Area ---
joined = gpd.sjoin(gdf_points, tnt_areas, how="left", predicate="within")

# --- Count Tickets per Area ---
ticket_counts = joined.groupby("TNT_NAME").size().reset_index(name="ticket_count")
# Merge the counts back into the TNT_Areas GeoDataFrame
tnt_areas = tnt_areas.merge(ticket_counts, on="TNT_NAME", how="left")
tnt_areas["ticket_count"] = tnt_areas["ticket_count"].fillna(0).astype(int)

# --- Create the Base Folium Map ---
# Center the map using the average coordinates from the ticket data.
map_center = [gdf_points.geometry.y.mean(), gdf_points.geometry.x.mean()]
m = folium.Map(location=map_center, control_scale=True, zoom_start=12)
HeatMap(heat_list, radius=15).add_to(m)

# --- Add a Title ---
title_html = '''
             <h3 align="center" style="font-size:15px;
             font-weight: bold;
             margin: 5px;">SYRCityline Total Requests 2021-Present</h3>
             '''
m.get_root().html.add_child(folium.Element(title_html))

# --- Add TNT_Areas Overlay with Boundaries ---
folium.GeoJson(
    tnt_areas.to_json(),
    name='TNT Areas',
    style_function=lambda feature: {
        'fillColor': 'transparent',
        'color': 'black',
        'weight': 2,
        'opacity': 0.4
    },
    tooltip=folium.GeoJsonTooltip(fields=['TNT_NAME'], aliases=['Area:'])
).add_to(m)

# --- Add Permanent Labels at Each Area's Centroid ---
for idx, row in tnt_areas.iterrows():
    # Calculate the centroid of the polygon
    centroid = row.geometry.centroid
    # Get the area label and ticket count
    area_label = row.get("TNT_NAME", "No Label")
    ticket_count = row.get("ticket_count", 0)
    # Build the label text with both the area name and its ticket count.
    label_text = f"{area_label} ({ticket_count})"

    # Create a marker using a DivIcon for a permanent label on the map.
    folium.Marker(
        [centroid.y, centroid.x],
        icon=folium.DivIcon(
            icon_size=(150, 36),
            icon_anchor=(0, 0),
            html=(
                f'<div style="font-size: 10pt; font-weight: bold; color: Black; '
                f'background: rgba(255,255,255,0.7); padding: 2px;">{label_text}</div>'
            )
        )
    ).add_to(m)

# --- Add Layer Control ---
folium.LayerControl().add_to(m)

# --- Save and Display the Map ---
m.save('heatmap_with_tnt_areas_counts.html')
m

In [139]:
# Set your selected assignee (update this value as needed)
selected_assignee = "Commissioner- Water"  # Replace with the desired assignee name

# Filter the dataframe by the selected assignee
df_assignee = df[df['Assignee_name'] == selected_assignee]

# Create a GeoDataFrame from the filtered ticket data
gdf_points = gpd.GeoDataFrame(
    df_assignee,
    geometry=gpd.points_from_xy(df_assignee.Lng, df_assignee.Lat),
    crs="EPSG:4326"
)

# --- Load TNT_Areas Data (Polygons) ---
tnt_areas = gpd.read_file('/content/Syracuse_TNT_Areas.geojson')
if tnt_areas.crs is None or tnt_areas.crs.to_string() != 'EPSG:4326':
    tnt_areas = tnt_areas.to_crs(epsg=4326)

# --- Spatial Join: Assign Each Ticket Its TNT_Area ---
joined = gpd.sjoin(gdf_points, tnt_areas, how="left", predicate="within")

# --- Count Tickets per Area for This Assignee ---
ticket_counts = joined.groupby("TNT_NAME").size().reset_index(name="ticket_count")
# Merge the counts back into the TNT_Areas GeoDataFrame
tnt_areas = tnt_areas.merge(ticket_counts, on="TNT_NAME", how="left")
tnt_areas["ticket_count"] = tnt_areas["ticket_count"].fillna(0).astype(int)

# --- Prepare Heatmap Data ---
heat_data = df_assignee.groupby(['Lat', 'Lng']).size().reset_index(name='count')
heat_list = heat_data[['Lat', 'Lng', 'count']].values.tolist()

m = folium.Map(location=map_center, control_scale=True, zoom_start=12)

# Add the HeatMap layer (for the selected assignee's data)
HeatMap(heat_list, radius=15).add_to(m)

# --- Add a Title ---
title_html = f'''
             <h3 align="center" style="font-size:15px;
             font-weight: bold;
             margin: 5px;">SYRCityline Requests 2021-Present for Assignee: {selected_assignee}</h3>
             '''
m.get_root().html.add_child(folium.Element(title_html))

# --- Add TNT_Areas Overlay with Boundaries ---
folium.GeoJson(
    tnt_areas.to_json(),
    name='TNT Areas',
    style_function=lambda feature: {
        'fillColor': 'transparent',
        'color': 'black',
        'weight': 2,
        'opacity': 0.4
    },
    tooltip=folium.GeoJsonTooltip(fields=['TNT_NAME'], aliases=['Area:'])
).add_to(m)

# --- Add Permanent Labels at Each Area's Centroid ---
for idx, row in tnt_areas.iterrows():
    # Calculate the centroid of the polygon
    centroid = row.geometry.centroid
    # Get the area label and ticket count
    area_label = row.get("TNT_NAME", "No Label")
    ticket_count = row.get("ticket_count", 0)
    # Build the label text with both the area name and its ticket count.
    label_text = f"{area_label} ({ticket_count})"

    # Create a marker using DivIcon for a permanent label on the map.
    folium.Marker(
        [centroid.y, centroid.x],
        icon=folium.DivIcon(
            icon_size=(150, 36),
            icon_anchor=(0, 0),
            html=(
                f'<div style="font-size: 10pt; font-weight: bold; color: Black; '
                f'background: rgba(255,255,255,0.7); padding: 2px;">{label_text}</div>'
            )
        )
    ).add_to(m)

# --- Add Layer Control ---
folium.LayerControl().add_to(m)

# --- Save and Display the Map ---
m.save('heatmap_with_tnt_areas_counts_assignee.html')
m


In [140]:
# Set your selected assignee (update this value as needed)
selected_assignee = "Cityline Operator- A"  # Replace with the desired assignee name

# Filter the dataframe by the selected assignee
df_assignee = df[df['Assignee_name'] == selected_assignee]

# Create a GeoDataFrame from the filtered ticket data
gdf_points = gpd.GeoDataFrame(
    df_assignee,
    geometry=gpd.points_from_xy(df_assignee.Lng, df_assignee.Lat),
    crs="EPSG:4326"
)

# --- Load TNT_Areas Data (Polygons) ---
tnt_areas = gpd.read_file('/content/Syracuse_TNT_Areas.geojson')
if tnt_areas.crs is None or tnt_areas.crs.to_string() != 'EPSG:4326':
    tnt_areas = tnt_areas.to_crs(epsg=4326)

# --- Spatial Join: Assign Each Ticket Its TNT_Area ---
joined = gpd.sjoin(gdf_points, tnt_areas, how="left", predicate="within")

# --- Count Tickets per Area for This Assignee ---
ticket_counts = joined.groupby("TNT_NAME").size().reset_index(name="ticket_count")
# Merge the counts back into the TNT_Areas GeoDataFrame
tnt_areas = tnt_areas.merge(ticket_counts, on="TNT_NAME", how="left")
tnt_areas["ticket_count"] = tnt_areas["ticket_count"].fillna(0).astype(int)

# --- Prepare Heatmap Data ---
heat_data = df_assignee.groupby(['Lat', 'Lng']).size().reset_index(name='count')
heat_list = heat_data[['Lat', 'Lng', 'count']].values.tolist()

m = folium.Map(location=map_center, control_scale=True, zoom_start=12)

# Add the HeatMap layer (for the selected assignee's data)
HeatMap(heat_list, radius=15).add_to(m)

# --- Add a Title ---
title_html = f'''
             <h3 align="center" style="font-size:15px;
             font-weight: bold;
             margin: 5px;">SYRCityline Requests 2021-Present for Assignee: {selected_assignee}</h3>
             '''
m.get_root().html.add_child(folium.Element(title_html))

# --- Add TNT_Areas Overlay with Boundaries ---
folium.GeoJson(
    tnt_areas.to_json(),
    name='TNT Areas',
    style_function=lambda feature: {
        'fillColor': 'transparent',
        'color': 'black',
        'weight': 2,
        'opacity': 0.4
    },
    tooltip=folium.GeoJsonTooltip(fields=['TNT_NAME'], aliases=['Area:'])
).add_to(m)

# --- Add Permanent Labels at Each Area's Centroid ---
for idx, row in tnt_areas.iterrows():
    # Calculate the centroid of the polygon
    centroid = row.geometry.centroid
    # Get the area label and ticket count
    area_label = row.get("TNT_NAME", "No Label")
    ticket_count = row.get("ticket_count", 0)
    # Build the label text with both the area name and its ticket count.
    label_text = f"{area_label} ({ticket_count})"

    # Create a marker using DivIcon for a permanent label on the map.
    folium.Marker(
        [centroid.y, centroid.x],
        icon=folium.DivIcon(
            icon_size=(150, 36),
            icon_anchor=(0, 0),
            html=(
                f'<div style="font-size: 10pt; font-weight: bold; color: Black; '
                f'background: rgba(255,255,255,0.7); padding: 2px;">{label_text}</div>'
            )
        )
    ).add_to(m)

# --- Add Layer Control ---
folium.LayerControl().add_to(m)

# --- Save and Display the Map ---
m.save('heatmap_with_tnt_areas_counts_assignee.html')
m


In [141]:
# Set your selected assignee (update this value as needed)
selected_assignee = "City Arborist"  # Replace with the desired assignee name

# Filter the dataframe by the selected assignee
df_assignee = df[df['Assignee_name'] == selected_assignee]

# Create a GeoDataFrame from the filtered ticket data
gdf_points = gpd.GeoDataFrame(
    df_assignee,
    geometry=gpd.points_from_xy(df_assignee.Lng, df_assignee.Lat),
    crs="EPSG:4326"
)

# --- Load TNT_Areas Data (Polygons) ---
tnt_areas = gpd.read_file('/content/Syracuse_TNT_Areas.geojson')
if tnt_areas.crs is None or tnt_areas.crs.to_string() != 'EPSG:4326':
    tnt_areas = tnt_areas.to_crs(epsg=4326)

# --- Spatial Join: Assign Each Ticket Its TNT_Area ---
joined = gpd.sjoin(gdf_points, tnt_areas, how="left", predicate="within")

# --- Count Tickets per Area for This Assignee ---
ticket_counts = joined.groupby("TNT_NAME").size().reset_index(name="ticket_count")
# Merge the counts back into the TNT_Areas GeoDataFrame
tnt_areas = tnt_areas.merge(ticket_counts, on="TNT_NAME", how="left")
tnt_areas["ticket_count"] = tnt_areas["ticket_count"].fillna(0).astype(int)

# --- Prepare Heatmap Data ---
heat_data = df_assignee.groupby(['Lat', 'Lng']).size().reset_index(name='count')
heat_list = heat_data[['Lat', 'Lng', 'count']].values.tolist()

m = folium.Map(location=map_center, control_scale=True, zoom_start=12)

# Add the HeatMap layer (for the selected assignee's data)
HeatMap(heat_list, radius=15).add_to(m)

# --- Add a Title ---
title_html = f'''
             <h3 align="center" style="font-size:15px;
             font-weight: bold;
             margin: 5px;">SYRCityline Requests 2021-Present for Assignee: {selected_assignee}</h3>
             '''
m.get_root().html.add_child(folium.Element(title_html))

# --- Add TNT_Areas Overlay with Boundaries ---
folium.GeoJson(
    tnt_areas.to_json(),
    name='TNT Areas',
    style_function=lambda feature: {
        'fillColor': 'transparent',
        'color': 'black',
        'weight': 2,
        'opacity': 0.4
    },
    tooltip=folium.GeoJsonTooltip(fields=['TNT_NAME'], aliases=['Area:'])
).add_to(m)

# --- Add Permanent Labels at Each Area's Centroid ---
for idx, row in tnt_areas.iterrows():
    # Calculate the centroid of the polygon
    centroid = row.geometry.centroid
    # Get the area label and ticket count
    area_label = row.get("TNT_NAME", "No Label")
    ticket_count = row.get("ticket_count", 0)
    # Build the label text with both the area name and its ticket count.
    label_text = f"{area_label} ({ticket_count})"

    # Create a marker using DivIcon for a permanent label on the map.
    folium.Marker(
        [centroid.y, centroid.x],
        icon=folium.DivIcon(
            icon_size=(150, 36),
            icon_anchor=(0, 0),
            html=(
                f'<div style="font-size: 10pt; font-weight: bold; color: Black; '
                f'background: rgba(255,255,255,0.7); padding: 2px;">{label_text}</div>'
            )
        )
    ).add_to(m)

# --- Add Layer Control ---
folium.LayerControl().add_to(m)

# --- Save and Display the Map ---
m.save('heatmap_with_tnt_areas_counts_assignee.html')
m


In [143]:
# Set your selected assignee (update this value as needed)
selected_assignee = "Water Emergency"  # Replace with the desired assignee name

# Filter the dataframe by the selected assignee
df_assignee = df[df['Assignee_name'] == selected_assignee]

# Create a GeoDataFrame from the filtered ticket data
gdf_points = gpd.GeoDataFrame(
    df_assignee,
    geometry=gpd.points_from_xy(df_assignee.Lng, df_assignee.Lat),
    crs="EPSG:4326"
)

# --- Load TNT_Areas Data (Polygons) ---
tnt_areas = gpd.read_file('/content/Syracuse_TNT_Areas.geojson')
if tnt_areas.crs is None or tnt_areas.crs.to_string() != 'EPSG:4326':
    tnt_areas = tnt_areas.to_crs(epsg=4326)

# --- Spatial Join: Assign Each Ticket Its TNT_Area ---
joined = gpd.sjoin(gdf_points, tnt_areas, how="left", predicate="within")

# --- Count Tickets per Area for This Assignee ---
ticket_counts = joined.groupby("TNT_NAME").size().reset_index(name="ticket_count")
# Merge the counts back into the TNT_Areas GeoDataFrame
tnt_areas = tnt_areas.merge(ticket_counts, on="TNT_NAME", how="left")
tnt_areas["ticket_count"] = tnt_areas["ticket_count"].fillna(0).astype(int)

# --- Prepare Heatmap Data ---
heat_data = df_assignee.groupby(['Lat', 'Lng']).size().reset_index(name='count')
heat_list = heat_data[['Lat', 'Lng', 'count']].values.tolist()

m = folium.Map(location=map_center, control_scale=True, zoom_start=12)

# Add the HeatMap layer (for the selected assignee's data)
HeatMap(heat_list, radius=15).add_to(m)

# --- Add a Title ---
title_html = f'''
             <h3 align="center" style="font-size:15px;
             font-weight: bold;
             margin: 5px;">SYRCityline Requests 2021-Present for Assignee: {selected_assignee}</h3>
             '''
m.get_root().html.add_child(folium.Element(title_html))

# --- Add TNT_Areas Overlay with Boundaries ---
folium.GeoJson(
    tnt_areas.to_json(),
    name='TNT Areas',
    style_function=lambda feature: {
        'fillColor': 'transparent',
        'color': 'black',
        'weight': 2,
        'opacity': 0.4
    },
    tooltip=folium.GeoJsonTooltip(fields=['TNT_NAME'], aliases=['Area:'])
).add_to(m)

# --- Add Permanent Labels at Each Area's Centroid ---
for idx, row in tnt_areas.iterrows():
    # Calculate the centroid of the polygon
    centroid = row.geometry.centroid
    # Get the area label and ticket count
    area_label = row.get("TNT_NAME", "No Label")
    ticket_count = row.get("ticket_count", 0)
    # Build the label text with both the area name and its ticket count.
    label_text = f"{area_label} ({ticket_count})"

    # Create a marker using DivIcon for a permanent label on the map.
    folium.Marker(
        [centroid.y, centroid.x],
        icon=folium.DivIcon(
            icon_size=(150, 36),
            icon_anchor=(0, 0),
            html=(
                f'<div style="font-size: 10pt; font-weight: bold; color: Black; '
                f'background: rgba(255,255,255,0.7); padding: 2px;">{label_text}</div>'
            )
        )
    ).add_to(m)

# --- Add Layer Control ---
folium.LayerControl().add_to(m)

# --- Save and Display the Map ---
m.save('heatmap_with_tnt_areas_counts_assignee.html')
m


In [144]:
# Set your selected assignee (update this value as needed)
selected_assignee = "Superintendent of Street Repair"  # Replace with the desired assignee name

# Filter the dataframe by the selected assignee
df_assignee = df[df['Assignee_name'] == selected_assignee]

# Create a GeoDataFrame from the filtered ticket data
gdf_points = gpd.GeoDataFrame(
    df_assignee,
    geometry=gpd.points_from_xy(df_assignee.Lng, df_assignee.Lat),
    crs="EPSG:4326"
)

# --- Load TNT_Areas Data (Polygons) ---
tnt_areas = gpd.read_file('/content/Syracuse_TNT_Areas.geojson')
if tnt_areas.crs is None or tnt_areas.crs.to_string() != 'EPSG:4326':
    tnt_areas = tnt_areas.to_crs(epsg=4326)

# --- Spatial Join: Assign Each Ticket Its TNT_Area ---
joined = gpd.sjoin(gdf_points, tnt_areas, how="left", predicate="within")

# --- Count Tickets per Area for This Assignee ---
ticket_counts = joined.groupby("TNT_NAME").size().reset_index(name="ticket_count")
# Merge the counts back into the TNT_Areas GeoDataFrame
tnt_areas = tnt_areas.merge(ticket_counts, on="TNT_NAME", how="left")
tnt_areas["ticket_count"] = tnt_areas["ticket_count"].fillna(0).astype(int)

# --- Prepare Heatmap Data ---
heat_data = df_assignee.groupby(['Lat', 'Lng']).size().reset_index(name='count')
heat_list = heat_data[['Lat', 'Lng', 'count']].values.tolist()

m = folium.Map(location=map_center, control_scale=True, zoom_start=12)

# Add the HeatMap layer (for the selected assignee's data)
HeatMap(heat_list, radius=15).add_to(m)

# --- Add a Title ---
title_html = f'''
             <h3 align="center" style="font-size:15px;
             font-weight: bold;
             margin: 5px;">SYRCityline Requests 2021-Present for Assignee: {selected_assignee}</h3>
             '''
m.get_root().html.add_child(folium.Element(title_html))

# --- Add TNT_Areas Overlay with Boundaries ---
folium.GeoJson(
    tnt_areas.to_json(),
    name='TNT Areas',
    style_function=lambda feature: {
        'fillColor': 'transparent',
        'color': 'black',
        'weight': 2,
        'opacity': 0.4
    },
    tooltip=folium.GeoJsonTooltip(fields=['TNT_NAME'], aliases=['Area:'])
).add_to(m)

# --- Add Permanent Labels at Each Area's Centroid ---
for idx, row in tnt_areas.iterrows():
    # Calculate the centroid of the polygon
    centroid = row.geometry.centroid
    # Get the area label and ticket count
    area_label = row.get("TNT_NAME", "No Label")
    ticket_count = row.get("ticket_count", 0)
    # Build the label text with both the area name and its ticket count.
    label_text = f"{area_label} ({ticket_count})"

    # Create a marker using DivIcon for a permanent label on the map.
    folium.Marker(
        [centroid.y, centroid.x],
        icon=folium.DivIcon(
            icon_size=(150, 36),
            icon_anchor=(0, 0),
            html=(
                f'<div style="font-size: 10pt; font-weight: bold; color: Black; '
                f'background: rgba(255,255,255,0.7); padding: 2px;">{label_text}</div>'
            )
        )
    ).add_to(m)

# --- Add Layer Control ---
folium.LayerControl().add_to(m)

# --- Save and Display the Map ---
m.save('heatmap_with_tnt_areas_counts_assignee.html')
m


In [146]:
# Set your selected assignee (update this value as needed)
selected_assignee = "Water-related Concerns"  # Replace with the desired assignee name

# Filter the dataframe by the selected assignee
df_assignee = df[df['Summary'] == selected_assignee]

# Create a GeoDataFrame from the filtered ticket data
gdf_points = gpd.GeoDataFrame(
    df_assignee,
    geometry=gpd.points_from_xy(df_assignee.Lng, df_assignee.Lat),
    crs="EPSG:4326"
)

# --- Load TNT_Areas Data (Polygons) ---
tnt_areas = gpd.read_file('/content/Syracuse_TNT_Areas.geojson')
if tnt_areas.crs is None or tnt_areas.crs.to_string() != 'EPSG:4326':
    tnt_areas = tnt_areas.to_crs(epsg=4326)

# --- Spatial Join: Assign Each Ticket Its TNT_Area ---
joined = gpd.sjoin(gdf_points, tnt_areas, how="left", predicate="within")

# --- Count Tickets per Area for This Assignee ---
ticket_counts = joined.groupby("TNT_NAME").size().reset_index(name="ticket_count")
# Merge the counts back into the TNT_Areas GeoDataFrame
tnt_areas = tnt_areas.merge(ticket_counts, on="TNT_NAME", how="left")
tnt_areas["ticket_count"] = tnt_areas["ticket_count"].fillna(0).astype(int)

# --- Prepare Heatmap Data ---
heat_data = df_assignee.groupby(['Lat', 'Lng']).size().reset_index(name='count')
heat_list = heat_data[['Lat', 'Lng', 'count']].values.tolist()

m = folium.Map(location=map_center, control_scale=True, zoom_start=12)

# Add the HeatMap layer (for the selected assignee's data)
HeatMap(heat_list, radius=15).add_to(m)

# --- Add a Title ---
title_html = f'''
             <h3 align="center" style="font-size:15px;
             font-weight: bold;
             margin: 5px;">SYRCityline Requests 2021-Present for Assignee: {selected_assignee}</h3>
             '''
m.get_root().html.add_child(folium.Element(title_html))

# --- Add TNT_Areas Overlay with Boundaries ---
folium.GeoJson(
    tnt_areas.to_json(),
    name='TNT Areas',
    style_function=lambda feature: {
        'fillColor': 'transparent',
        'color': 'black',
        'weight': 2,
        'opacity': 0.4
    },
    tooltip=folium.GeoJsonTooltip(fields=['TNT_NAME'], aliases=['Area:'])
).add_to(m)

# --- Add Permanent Labels at Each Area's Centroid ---
for idx, row in tnt_areas.iterrows():
    # Calculate the centroid of the polygon
    centroid = row.geometry.centroid
    # Get the area label and ticket count
    area_label = row.get("TNT_NAME", "No Label")
    ticket_count = row.get("ticket_count", 0)
    # Build the label text with both the area name and its ticket count.
    label_text = f"{area_label} ({ticket_count})"

    # Create a marker using DivIcon for a permanent label on the map.
    folium.Marker(
        [centroid.y, centroid.x],
        icon=folium.DivIcon(
            icon_size=(150, 36),
            icon_anchor=(0, 0),
            html=(
                f'<div style="font-size: 10pt; font-weight: bold; color: Black; '
                f'background: rgba(255,255,255,0.7); padding: 2px;">{label_text}</div>'
            )
        )
    ).add_to(m)

# --- Add Layer Control ---
folium.LayerControl().add_to(m)

# --- Save and Display the Map ---
m.save('heatmap_with_tnt_areas_counts_assignee.html')
m


In [155]:

import pandas as pd
import folium
from folium.plugins import HeatMap, HeatMapWithTime


# single comment generated by OpenAI ChatGPT-o3-mni-high
# Load your dataset
# For example, if your data is in a CSV file:
df = pd.read_csv("/content/SYRCityline_Requests_(2021-Present)_Cleaned.csv")

# Convert the time columns to datetime
df['Created_at_local'] = pd.to_datetime(df['Created_at_local'])
df['Closed_at_local'] = pd.to_datetime(df['Closed_at_local'], errors='coerce')

# Determine the overall time range:
# Start at the earliest ticket open time
start_time = df['Created_at_local'].min()
# End at the latest closed time, or if some tickets are still open, use the current time
end_time = df['Closed_at_local'].max()
if pd.isnull(end_time) or end_time < pd.Timestamp.now():
    end_time = pd.Timestamp.now()

# Create a time index – here we use hourly intervals, but you can adjust as needed.
time_index = pd.date_range(start=start_time, end=end_time, freq='MS')

# Build a list where each element corresponds to a time slice:
# for each time, filter active tickets (opened but not yet closed) and group by location.
heat_data_time = []  # List of lists for each time slice
time_labels = []     # Corresponding time labels

for current_time in time_index:
    # A ticket is active if it was opened before (or at) the current time
    # and if it is not closed OR closed after the current time.
    active_tickets = df[
        (df['Created_at_local'] <= current_time) &
        ((df['Closed_at_local'].isnull()) | (df['Closed_at_local'] > current_time))
    ]
    active_count = active_tickets.shape[0]

    # Group the active tickets by their coordinates and count occurrences.
    grouped = active_tickets.groupby(['Lat', 'Lng']).size().reset_index(name='count')

    # Create a list of points in the format [latitude, longitude, weight]
    points = grouped[['Lat', 'Lng', 'count']].values.tolist()
    heat_data_time.append(points)

    time_labels.append(f"{current_time.strftime('%Y-%m')} (Open: {active_count})")

print(time_labels)
print(len(heat_data_time[10]))
# Create a base Folium map centered on the average location
map_center = [df['Lat'].mean(), df['Lng'].mean()]

m_time = folium.Map(location=map_center,
               control_scale=True,
               #zoom_control=False,
               zoom_start=12)

# --- Add TNT_Areas Overlay with Boundaries ---
folium.GeoJson(
    tnt_areas.to_json(),
    name='TNT Areas',
    style_function=lambda feature: {
        'fillColor': 'transparent',
        'color': 'black',
        'weight': 2,
        'opacity': 0.4
    },
    tooltip=folium.GeoJsonTooltip(fields=['TNT_NAME'], aliases=['Area:'])
).add_to(m_time)

    # Create a marker using DivIcon for a permanent label on the map.
folium.Marker(
        [centroid.y, centroid.x],
        icon=folium.DivIcon(
            icon_size=(150, 36),
            icon_anchor=(0, 0),
            html=(
                f'<div style="font-size: 10pt; font-weight: bold; color: Black; '
                f'background: rgba(255,255,255,0.7); padding: 2px;">{label_text}</div>'
            )
        )
    ).add_to(m)

HeatMapWithTime(heat_data_time,
                index=time_labels,
                auto_play=True,
                radius=15,


                ).add_to(m_time)
# Save the map to an HTML file (or display it in a Jupyter notebook)
m_time.save('heatmap_time.html')

m_time

<ipython-input-155-a3785c0f0b77>:13: UserWarning:

Could not infer format, so each element will be parsed individually, falling back to `dateutil`. To ensure parsing is consistent and as-expected, please specify a format.



['2021-07 (Open: 27)', '2021-08 (Open: 707)', '2021-09 (Open: 2125)', '2021-10 (Open: 2504)', '2021-11 (Open: 689)', '2021-12 (Open: 934)', '2022-01 (Open: 290)', '2022-02 (Open: 256)', '2022-03 (Open: 344)', '2022-04 (Open: 402)', '2022-05 (Open: 506)', '2022-06 (Open: 510)', '2022-07 (Open: 400)', '2022-08 (Open: 279)', '2022-09 (Open: 244)', '2022-10 (Open: 196)', '2022-11 (Open: 185)', '2022-12 (Open: 212)', '2023-01 (Open: 235)', '2023-02 (Open: 236)', '2023-03 (Open: 251)', '2023-04 (Open: 371)', '2023-05 (Open: 504)', '2023-06 (Open: 537)', '2023-07 (Open: 733)', '2023-08 (Open: 710)', '2023-09 (Open: 495)', '2023-10 (Open: 803)', '2023-11 (Open: 673)', '2023-12 (Open: 788)', '2024-01 (Open: 868)', '2024-02 (Open: 767)', '2024-03 (Open: 753)', '2024-04 (Open: 743)', '2024-05 (Open: 760)', '2024-06 (Open: 963)', '2024-07 (Open: 1172)', '2024-08 (Open: 1541)', '2024-09 (Open: 1967)', '2024-10 (Open: 2105)', '2024-11 (Open: 2636)', '2024-12 (Open: 3537)', '2025-01 (Open: 4559)', '2

<ipython-input-70-9eb70f1596d5>:14: UserWarning:

CRS mismatch between the CRS of left geometries and the CRS of right geometries.
Use `to_crs()` to reproject one of the input geometries to match the CRS of the other.

Left CRS: None
Right CRS: EPSG:4326




        Unnamed: 0             X             Y          Id  \
0                1 -8.472894e+06  5.319007e+06  18198655.0   
1                2 -8.479295e+06  5.320378e+06  18214945.0   
2                3 -8.476745e+06  5.313388e+06  18214845.0   
3                4 -8.477781e+06  5.324004e+06  18214835.0   
4                5 -8.475632e+06  5.320393e+06  18214821.0   
...            ...           ...           ...         ...   
112853      112854 -8.476356e+06  5.321566e+06  18051735.0   
112854      112855 -8.474630e+06  5.318870e+06  18048719.0   
112855      112856 -8.473784e+06  5.321033e+06  18214965.0   
112856      112857 -8.476233e+06  5.315504e+06  18214963.0   
112857      112858 -8.473183e+06  5.316950e+06  18214961.0   

                                                  Summary  Rating  \
0                               Sewer Back-ups (INTERNAL)       1   
1                            Other Sewer-related Concerns       1   
2       Report Improperly Set Out Trash or Recyc

    TNT_NAME  Created_at_Local
0   Downtown              2253
1   Eastside             20568
2   Eastwood             12053
3  Lakefront               911
4  Northside             28075
5  Southside             22947
6     Valley              7860
7   Westside             18160


TypeError: Object of type Point is not JSON serializable